In [ ]:
import sys
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt

triskele_path = Path('../triskele/python/')
sys.path.append(str(triskele_path.resolve()))
import triskele

## List raster files

In [ ]:
layers_files = [
    '../Data/phase1_rasters/DEM+B_C123/UH17_GEM051_TR.tif',
    '../Data/phase1_rasters/DEM_C123_3msr/UH17_GEG051_TR.tif',
    '../Data/phase1_rasters/DEM_C123_TLI/UH17_GEG05_TR.tif',
    '../Data/phase1_rasters/DSM_C12/UH17c_GEF051_TR.tif',
    '../Data/phase1_rasters/Intensity_C1/UH17_GI1F051_TR.tif',
    '../Data/phase1_rasters/Intensity_C2/UH17_GI2F051_TR.tif',
    '../Data/phase1_rasters/Intensity_C3/UH17_GI3F051_TR.tif',
    #'../Data/ground_truth/2018_IEEE_GRSS_DFC_GT_TR.tif'
]

## Define dataset dependent raster filtering

In [ ]:
def DFC_filter(raster):
    ## Remove extrem values
    #raster[raster == raster.max()] = raster[raster != raster.max()].max()
    raster[raster > 1e4] = raster[raster < 1e4].max()
    #raster[raster == np.finfo(raster.dtype).max] = raster[raster != raster.max()].max()

## Load rasters data

In [ ]:
layers = list()

for file in layers_files:
    print('Loading {}'.format(file))
    layer = triskele.read(file)
    DFC_filter(layer)
    layers.append(layer)

layers_stack = np.stack(layers, axis=2)

## Display rasters

In [ ]:
for i in range(layers_stack.shape[2]):
    plt.figure(figsize=(16*2,3*2))
    plt.imshow(layers_stack[:,:,i])
    plt.colorbar()
    plt.title(layers_files[i])
    plt.show()

## Attributes filter with TRISKELE !

In [ ]:
area = np.array([10, 100, 1e3, 1e4, 1e5])
sd   = np.array([0.5,0.9,0.99,0.999,0.9999])#,1e4,1e5,5e5])
moi  = np.array([0.01,0.02,0.03,0.04,0.05,0.06,0.07,0.08,0.09,0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9,0.99])

t = triskele.Triskele(layers_stack[:,:,:], verbose=False)
attributes = t.filter(tree='tos-tree',
                      area=area,
                      standard_deviation=sd,
                      moment_of_inertia=moi
                     )
attributes.shape

for i in range(attributes.shape[2]-1):
    plt.figure(figsize=(16*2,3*2))
    plt.imshow(attributes[:,:,i])
    plt.colorbar()
    plt.show()
    plt.figure(figsize=(16*2,3*2))
    plt.imshow(attributes[:,:,i+1].astype(np.float) - attributes[:,:,i])
    plt.colorbar()
    #plt.title(layers_files[i])
plt.show()
plt.figure(figsize=(16*2,3*2))
plt.imshow(attributes[:,:,-1])
plt.colorbar()
plt.show()


## Classification vectors

In [ ]:
X = attributes.reshape(-1, attributes.shape[2])

(attributes[0,0] == X[0]).all()

In [ ]:
labels_file = Path('../Data/ground_truth/2018_IEEE_GRSS_DFC_GT_TR.tif')
labels = triskele.read(labels_file)
display(labels.shape)

plt.figure(figsize=(16*2,3*2))
plt.imshow(labels)
plt.colorbar()
plt.show()

In [ ]:
Y = labels.reshape(-1)

X.shape, Y.shape

## Random Forest Classifier

In [ ]:
import importlib
from sklearn import metrics
from sklearn.ensemble import RandomForestClassifier
import pickle
sys.path.insert(0, '..')
import CrossValidationGenerator as cvg

In [ ]:
importlib.reload(cvg)

In [ ]:
from sklearn import metrics
import pandas as pd


def scores(actual, prediction):
    ct = pd.crosstab(prediction, actual,
            rownames=['Prediction'], colnames=['Reference'],
            margins=True, margins_name='Total',
            normalize=False # all, index, columns
            )
    display(ct)
    
    scores = metrics.precision_recall_fscore_support(actual, prediction)
    print(metrics.classification_report(actual, prediction))    

In [ ]:
cv_labels = np.zeros(labels[:].shape)

for xtrain, xtest, ytrain, ytest, train_index in cvg.CVG(attributes[:], labels[:], 10, 1): 
    rfc = RandomForestClassifier(n_jobs=-1, random_state=0, n_estimators=100, verbose=True)
    rfc.fit(xtrain, ytrain)
    
    ypred = rfc.predict(xtest)
    
    display(ytest.shape, ypred.shape)
    
    scores(ytest, ypred)
    
    cv_labels[:,train_index == False] = ypred.reshape(cv_labels.shape[0], -1)
    

In [ ]:
def show(im):
    plt.figure(figsize=(16*2,3*2))
    plt.imshow(im)
    plt.colorbar()
    plt.show()

In [ ]:
show(labels)
show(cv_labels)

In [ ]:
labels.shape

In [ ]:
np.arange(238400).reshape(-1, 4768)

In [ ]:
with open('../Res/classifier_0.pkl', 'wb') as f:
    pickle.dump(rfc, f)

In [ ]:
Yp = Y.copy()

Yp[training == False] = rfc.predict(X[training == False])

In [ ]:
plt.figure(figsize=(16*2,3*2))
plt.imshow(Y.reshape(labels.shape))
plt.colorbar()
plt.show()

plt.figure(figsize=(16*2,3*2))
plt.imshow(Yp.reshape(labels.shape))
plt.colorbar()
plt.show()

plt.figure(figsize=(16*2,3*2))
plt.imshow(Yp.reshape(labels.shape).astype(np.float) - labels)
plt.colorbar()
plt.show()

In [ ]:
class cvg:
    def __init__(self, attributes, ground_truth, order_dim=0, n_test=2):      
        self._tests_left = n_test
        
        if attributes.shape[0] != ground_truth.shape[0] or \
           attributes.shape[1] != ground_truth.shape[1] :
                raise ValueError('attributes and ground_truth must have the same 2D shape')
        
    def __iter__(self):
        return self
    
    def __next__(self):
        if self._tests_left == 0:
            raise StopIteration
        
        train_filter = np.arange(attributes.shape) < (Y.size * .50)

        Xtrain = 42
        Xtest = 432
        Ytrain = 12
        Ytest = 123
        
        return (Xtrain, Xtest, Ytrain, Ytest)

In [ ]:
cvg(attributes, labels[:,:-1])